### Подключение библиотек

In [41]:
from bs4 import BeautifulSoup as bs
import requests
import pandas as pd
import json
import pymupdf
import io
import re
import glob

# Парсинг сайта

#### Получение информации с сайта

In [42]:
# GET - запрос
url = 'https://store.steampowered.com/search/?supportedlang=russian?l=russian?filter=topsellers&ndl=1'
page = requests.get(url)
page.encoding = 'utf-8'

In [43]:
page.status_code

200

In [44]:
soup = bs(page.text, 'html.parser')

In [45]:
page.text

'<!DOCTYPE html>\n<html class=" responsive DesktopUI" lang="en">\n<head>\n\t<meta http-equiv="Content-Type" content="text/html; charset=UTF-8">\n\t\t\t<meta name="viewport" content="width=device-width,initial-scale=1">\n\t\t<meta name="theme-color" content="#171a21">\n\t\t<title>Steam Search</title>\n\t<link rel="shortcut icon" href="/favicon.ico" type="image/x-icon">\n\n\t\n\t\n\t<link href="https://store.fastly.steamstatic.com/public/shared/css/motiva_sans.css?v=YzJgj1FjzW34&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css">\n<link href="https://store.fastly.steamstatic.com/public/shared/css/shared_global.css?v=EkTkrKqfnPCh&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css">\n<link href="https://store.fastly.steamstatic.com/public/shared/css/buttons.css?v=BZhNEtESfYSJ&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css">\n<link href="https://store.fastly.steamstatic.com/public/css/v6/store.css?v=bqby8rk1zf3h&amp;l=english&amp;_cdn=fastly" rel="st

In [46]:
soup

<!DOCTYPE html>

<html class="responsive DesktopUI" lang="en">
<head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="width=device-width,initial-scale=1" name="viewport"/>
<meta content="#171a21" name="theme-color"/>
<title>Steam Search</title>
<link href="/favicon.ico" rel="shortcut icon" type="image/x-icon"/>
<link href="https://store.fastly.steamstatic.com/public/shared/css/motiva_sans.css?v=YzJgj1FjzW34&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css"/>
<link href="https://store.fastly.steamstatic.com/public/shared/css/shared_global.css?v=EkTkrKqfnPCh&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css"/>
<link href="https://store.fastly.steamstatic.com/public/shared/css/buttons.css?v=BZhNEtESfYSJ&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css"/>
<link href="https://store.fastly.steamstatic.com/public/css/v6/store.css?v=bqby8rk1zf3h&amp;l=english&amp;_cdn=fastly" rel="stylesheet" type="text/css"/>
<link h

In [73]:
df = pd.read_csv('games.csv').drop('Unnamed: 0', axis=1)

In [74]:
result_list = {'title': df['title'].tolist(), 'description': df['description'].tolist(), 'date': df['date'].tolist(), 'tags': df['tags'].tolist(), 'rating': df['rating'].tolist()}

### Алгоритм

In [9]:
def split_text(text, max_length=5000):
    # Разбивает текст на куски не длиннее max_length, по предложениям или словам
    paragraphs = text.split('.')
    chunks = []
    for paragraph in paragraphs:
        if not paragraph.strip():
            continue
        # Разбиваем на части, чтобы не превышать лимит
        wrapped = textwrap.wrap(paragraph, max_length, break_long_words=False, replace_whitespace=False)
        chunks.extend(wrapped)
    return chunks

def translate_large_text(text, target='ru'):
    chunks = split_text(text)
    translated_chunks = []
    translator = GoogleTranslator(source='auto', target=target)
    for chunk in chunks:
        translated = translator.translate(chunk)
        translated_chunks.append(translated)
    return '.'.join(translated_chunks)


In [10]:
from deep_translator import GoogleTranslator
import textwrap
from langdetect import detect

for page in range(1, 21):  # 20 страниц × 25 игр = 500 игр
    url = f"https://store.steampowered.com/search/?category1=998?filter=globaltopsellers&page={page}"
    print(url)
    page = requests.get(url)
    page.encoding = 'utf-8'
    soup = bs(page.text, 'html.parser')
    games = soup.find_all('a', class_='search_result_row')[:200]
    for idx, game in enumerate(games, 1):
        title = game.find('span', class_='title').text.strip()
        if title.__contains__('Steam Deck'):
            continue
        print(title)
        result_list['title'].append(title)
        date = game.find('div', class_='search_released').text.strip()
        print(date)
        result_list['date'].append(date)
        game_url = game['href']
        print(game_url.replace('?', '?l=russian?'))
        game_page = requests.get(game_url[:game_url.find('?')] + '?l=russian')
        game_soup = bs(game_page.text, 'html.parser')
        description_tag = game_soup.find("div", {"id": "game_area_description"})
        if description_tag:
            description = description_tag.text.replace('\n', ' ').replace('\t','').replace('Об этой игре','').replace('Об этом ПО','').strip()
            if description == "":
                description = 'Нет описания'
        else:
            description = 'Нет описания'
        if (detect(description) == 'en'):
            if (len(description) > 4999):
                description = translate_large_text(description)
            else:
                description = GoogleTranslator(source='auto', target='ru').translate(description)
        print(description)
        result_list['description'].append(description)
        tags = ', '.join([tag.text.strip() for tag in game_soup.select('.glance_tags.popular_tags a')])
        print(tags)
        result_list['tags'].append(tags)
        if game_soup.find('div', class_='summary column'):
            if game_soup.find('div', class_='summary column').text.__contains__('No') or game_soup.find('div', class_='summary column').text.__contains__('Нет'):
                review_text = 'Нет пользовательской оценки'
            else:
                review_text = game_soup.find('meta', itemprop='ratingValue').attrs['content'] + ' / 10'
        else:
            review_text = 'Нет пользовательской оценки'
        print(review_text + "\n")
        result_list['rating'].append(review_text)

https://store.steampowered.com/search/?category1=998?filter=globaltopsellers&page=1
Counter-Strike 2
21 Aug, 2012
https://store.steampowered.com/app/730/CounterStrike_2/?l=russian?snr=1_7_7_230_150_1
Более двух десятилетий Counter-Strike служит примером первоклассной соревновательной игры, путь развития которой определяют миллионы игроков со всего мира. Теперь пришло время нового этапа — Counter-Strike 2.Counter-Strike 2 — это бесплатное улучшение для CS:GO, которое знаменует собой крупнейший технологический скачок в истории серии. Оно разработано на движке Source 2 и модернизирует игру благодаря реалистичному и физически корректному рендерингу, организации сети по последнему слову технологий и улучшенным инструментам для мастерской сообщества.Кроме представленного в 1999 году классического игрового процесса, завязанного на достижении цели, Counter-Strike 2 включает:новые рейтинги CS и обновлённый премьер-режим;глобальные и региональные таблицы лидеров;улучшенные и воссозданные с нуля 

In [75]:
print(len(result_list['title']))
print(len(result_list['rating']))
print(len(result_list['date']))
print(len(result_list['description']))
print(len(result_list['tags']))

500
500
500
500
500


In [76]:
print(result_list)

{'title': ['Counter-Strike 2', 'Clair Obscur: Expedition 33', 'HELLDIVERS™ 2', 'Cyberpunk 2077', 'Dota 2', 'RoadCraft', "Baldur's Gate 3", 'DOOM: The Dark Ages', 'Tainted Grail: The Fall of Avalon', 'The Elder Scrolls IV: Oblivion Remastered', 'Schedule I', 'R.E.P.O.', 'Red Dead Redemption 2', 'Warframe', 'Warhammer 40,000: Space Marine 2', 'FANTASY LIFE i: The Girl Who Steals Time', 'Rust', 'Apex Legends™', 'War Thunder', 'Monster Train 2', 'Drive Beyond Horizons', 'Warhammer 40,000: Rogue Trader', 'PUBG: BATTLEGROUNDS', 'Marvel Rivals', 'Split Fiction', 'EA SPORTS FC™ 25', 'Total War: WARHAMMER III', 'Stellaris', 'Ready or Not', 'Enshrouded', 'The Witcher 3: Wild Hunt', 'ELDEN RING', 'The Last of Us™ Part II Remastered', 'Dead by Daylight', 'Destiny 2', 'Warhammer 40,000: Darktide', 'Crusader Kings III', 'RuneScape: Dragonwilds', 'Euro Truck Simulator 2', "Tom Clancy's Rainbow Six® Siege", 'Path of Exile 2', 'Farming Simulator 25', 'Blue Prince', 'STAR WARS™ Battlefront™ II', 'V Risi

### Создание датафрейма и запись в файл

In [77]:
file_name = 'games.csv'
df = pd.DataFrame(data=result_list)
df.to_csv(file_name)
df.head()

title  \
0             Counter-Strike 2   
1  Clair Obscur: Expedition 33   
2                HELLDIVERS™ 2   
3               Cyberpunk 2077   
4                       Dota 2   

                                         description          date  \
0  Более двух десятилетий Counter-Strike служит п...  21 Aug, 2012   
1  Раз в год Художница просыпается и рисует на Мо...  24 Apr, 2025   
2  Последняя линия нападения галактики.Станьте Ад...   8 Feb, 2024   
3  Cyberpunk 2077 — приключенческая ролевая игра ...   9 Dec, 2020   
4  Самая популярная игра в SteamЕжедневно миллион...   9 Jul, 2013   

                                                tags   rating  
0  Шутер от первого лица, Шутер, Для нескольких и...   9 / 10  
1  Пошаговые сражения, Глубокий сюжет, Фэнтези, И...  10 / 10  
2  Сетевой кооператив, Игрок против ИИ, Шутер от ...   7 / 10  
3  Киберпанк, Открытый мир, Нагота, Ролевая игра,...   9 / 10  
4  Бесплатная игра, MOBA, Для нескольких игроков,...   9 / 10

In [78]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   title        500 non-null    object
 1   description  500 non-null    object
 2   date         500 non-null    object
 3   tags         499 non-null    object
 4   rating       500 non-null    object
dtypes: object(5)
memory usage: 19.7+ KB


# Парсинг PDF файла

In [79]:
# загрузка в list пути всех нужных pdf файлов
all_pdf = glob.glob(r"PDF2\*.pdf")
pattern = r'(\d{1,2})\s([а-я]{3})\sв\s(\d{2}:\d{2})'

In [80]:
len(all_pdf)

11

In [81]:
all_pdf

['PDF2\\Cocoapods, Carthage, SPM как выбрать менеджер зависимостей в iOS.pdf',
 'PDF2\\imgonline-com-ua-site2pdfB28eKGLy6EjA.pdf',
 'PDF2\\OSINT & Hacking — как работает фишинг для нельзяграма _ Хабр3.pdf',
 'PDF2\\Быстрое начало работы с Gitlab CICD.pdf',
 'PDF2\\Генеральный директор Mozilla покинула свой пост _ Хабр.pdf',
 'PDF2\\ИИ-агенты в Альфа-Банке_ нейросети создают автотесты без участия человека _ Хабр.pdf',
 'PDF2\\Инструменты наблюдаемости, о которых нужно знать в 2023 году.pdf',
 'PDF2\\История российской науки_ напишем вместе_ _ Хабр.pdf',
 'PDF2\\Как создать аппаратный эмулятор CD-ROM без паяльника _ Хабр.pdf',
 'PDF2\\Может ли chatGPT забронировать столик в ресторане через WhatsApp.pdf',
 'PDF2\\Новые утечки.pdf']

#### Получение информации с файла

In [82]:
for i in all_pdf:
    pdf_document = i
    doc = pymupdf.open(pdf_document)
    print("Исходный документ: ", doc)
    print("\nКоличество страниц: %i\n\n------------------\n\n" % doc.page_count)
    print(doc.metadata)
    for current_page in range(len(doc)):
        page = doc.load_page(current_page)
        page_text = page.get_text("text")
        print("Стр. ", current_page+1, "\n")
        print(page_text)

Исходный документ:  Document('PDF2\Cocoapods, Carthage, SPM как выбрать менеджер зависимостей в iOS.pdf')

Количество страниц: 29

------------------


{'format': 'PDF 1.7', 'title': 'Aspose', 'author': 'Aspose', 'subject': 'Aspose', 'keywords': '', 'creator': 'Aspose Pty Ltd.', 'producer': 'Aspose.PDF for .NET 23.2.0', 'creationDate': "D:20230320172822+00'00'", 'modDate': "D:20230320172822+00'00'", 'trapped': '', 'encryption': None}
Стр.  1 

117.94
Рейтинг
red_mad_robot
№1 в разработке цифровых решений для бизнеса
 6 часов назад
Средний18 мин
redmadrobot
Cocoapods, Carthage, SPM: как выбрать
менеджер зависимостей в iOS
179
Блог компании red_mad_robot
, 
Разработка под iOS*
FAQ
КАК СТАТЬ АВТОРОМ

Стр.  2 

Старший iOS-разработчик red_mad_robot Аня Кочешкова
рассказывает, чем отличаются три менеджера зависимостей, в каких
случаях и для каких задач подойдёт тот или иной. Материал будет
полезен джун-специалистам, которые только начали погружаться
в разработку: специально для них подробно

In [83]:

def extract_text_from_pdf(pdf):
    doc = pymupdf.open(pdf)
    print(pdf)
    text = ''
    for current_page in range(len(doc)):
        page = doc.load_page(current_page)
        page_text = page.get_text("text")
        text += page_text
    return text.replace('8 минTAU15', '').replace('+1','1').replace('+9','9').replace('9 мин','').replace('+7','7').replace('Средний1','').replace('Простой','').replace('1.1K','1100').replace('3 мин','').replace('Простой  3 мин','').replace('Cloud4Y OSINT','OSINT').replace('Cloud4Y 5 часов назад','5 часов назад').replace('КАК СТАТЬ АВТОРОМ','').replace('1 мин','').replace('Простой9 мин','').replace('8 мин','').replace('5 мин','').replace('zubarek','').replace('Средний18 мин','').replace('5 минArnak', '').replace('redmadrobot','').replace('ru_vds','').replace('Средний19 минartyomsoft', '').replace('Средний18 минredmadrobot', '').replace('5 минzubarek', '').replace('technokratiya','').replace('5 часов назад\tCloud4Y','5 часов назад').replace('Простой3 мин','').replace('Exosphere ','').replace('AlfaTeam ','').replace('AnnieBronson ','').replace('redmadrobot ','').replace('red_mad_robot ','').replace('Средний18 мин ','').replace('artyomsoft','').replace('Arnak','').replace('RUVDS.com','').replace('VDS/VPS-хостинг. Скидка 15% по коду HABR15','').replace('Средний19 мин','').replace('RUVDS.com VDS/VPS-хостинг. Скидка 15% по коду HABR15','').replace('TAU15','').replace('RUVDS.com VDS/VPS-хостинг. Скидка 15% по коду HABR15','')


### Алгоритм

In [84]:

def pars_pdf(text):
    text2 = text.split('\n')
    text2 = [x for x in text2 if x.strip()]
    name = ''
    if 'Рейтинг' in text2:
        num = text2.index('Рейтинг')
        raiting = text2[num - 1]
    for i in range(0, len(text2) - 1):
        if 'назад' in text2[i] and name == '':
            num3 = i
            date_publish = text2[num3].strip()
            if text2[num3 + 1].__contains__('Cloud4Y'):
                name = text2[num3 + 2] + ' ' + text2[num3 + 3]
            else:
                if not f'{text2[num3 + 2]}'.strip().isalnum():
                    name = text2[num3 + 1] + ' ' + text2[num3 + 2]
                else:
                    name = text2[num3 + 1]
        elif re.search(pattern, text2[i]):
            num3 = i
            date_publish = text2[num3].strip()
            if text2[num3 + 1].__contains__('Cloud4Y'):
                name = text2[num3 + 2] + ' ' + text2[num3 + 3]
            else:
                if not f'{text2[num3 + 2]}'.strip().isalnum():
                    name = text2[num3 + 1] + ' ' + text2[num3 + 2]
                else:
                    name = text2[num3 + 1]
        if 'Хабы' in text2[i]:
            hubs = ''
            j = i
            while not f'{text2[j]}'.strip().isnumeric() and not text2[j].__contains__('Редакторский дайджест'):
                hubs += text2[j] + ' '
                j += 1
            break
    return name, raiting, date_publish, hubs



In [85]:
Brak = []
result_list1 = {'title': [], 'description': [], 'date': [], 'tags': [], 'rating': []}

In [86]:
for pdf in all_pdf:
    try:
        x = extract_text_from_pdf(pdf)
        N, R, D, H = pars_pdf(x)
        D2 = ''.join(x).replace('\n', ' ')
        result_list1['title'].append(N)
        print(f'{N}\t')
        result_list1['rating'].append(R)
        print(f'{R}\t')
        result_list1['date'].append(D)
        print(f'{D}\t')
        result_list1['description'].append(D2)
        print(f'{D2}\t')
        result_list1['tags'].append(H)
        print(f'{H}\n')
        result_list['title'].append(N)
        result_list['rating'].append(R)
        result_list['date'].append(D)
        result_list['description'].append(D2)
        result_list['tags'].append(H)
    except Exception as e:
        print(e)
        Brak.append(pdf)


PDF2\Cocoapods, Carthage, SPM как выбрать менеджер зависимостей в iOS.pdf
Cocoapods, Carthage, SPM: как выбрать менеджер зависимостей в iOS	
117.94	
6 часов назад	
117.94 Рейтинг red_mad_robot №1 в разработке цифровых решений для бизнеса  6 часов назад   Cocoapods, Carthage, SPM: как выбрать менеджер зависимостей в iOS 179 Блог компании red_mad_robot ,  Разработка под iOS* FAQ  Старший iOS-разработчик Аня Кочешкова рассказывает, чем отличаются три менеджера зависимостей, в каких случаях и для каких задач подойдёт тот или иной. Материал будет полезен джун-специалистам, которые только начали погружаться в разработку: специально для них подробно объясняем, что такое семантическое версионирование, как устроены модули кода и в чём разница между динамическими и статическими библиотеками. Что такое менеджер зависимостей и зачем он нужен В современной разработке зависимость — это написанный кем-то другим код, который используется в вашей программе. Добавление зависимости позволяет воспользоват

### Создание датафрейма и запись в файл

In [87]:
file_name = 'pdf_files.csv'
df = pd.DataFrame(data=result_list1)
df.to_csv(file_name)

In [88]:
df

title  \
0   Cocoapods, Carthage, SPM: как выбрать менеджер...   
1   OSINT & Hacking — как работает фишинг для нель...   
2   OSINT & Hacking — как работает фишинг для нель...   
3   Быстрое начало работы с Gitlab CI/CD: пайплайн...   
4     Генеральный директор Mozilla покинула свой пост   
5   ИИ-агенты в Альфа-Банке: нейросети создают авт...   
6   Инструменты наблюдаемости, о которых нужно зна...   
7      История российской науки: напишем вместе? 1.3K   
8   Как создать аппаратный эмулятор CD-ROM без пая...   
9   Может ли chatGPT забронировать столик в рестор...   
10     Новые утечки. Что мы знаем о выходе Windows 12   

                                          description            date  \
0   117.94 Рейтинг red_mad_robot №1 в разработке ц...   6 часов назад   
1   71.07 Рейтинг Cloud4Y #1 Корпоративный облачны...   5 часов назад   
2   71.07 Рейтинг Cloud4Y #1 Корпоративный облачны...   5 часов назад   
3   4.29 Оценка 280.79 Рейтинг Southbridge Обеспеч...    2 часа назад   
4   Митчелл Бейкер, гендиректор Mozilla с 2020 год...  12 минут назад   
5   404.32 Рейтинг Альфа-Банк Лучший мобильный бан...    2 часа назад   
6   2376.9 Рейтинг   Автор оригинала: Lahiru Hewaw...    4 часа назад   
7   4.58 Оценка 353.18 Рейтинг Хабр Экосистема для...  10 часов назад   
8   2394.92 Рейтинг   Несмотря на то, что постепен...  20 мар в 14:00   
9    Идея А почему бы не использовать возможности ...   6 часов назад   
10  4.74 Оценка 414.35 Рейтинг getmatch Рассказыва...    4 часа назад   

                                                 tags   rating  
0   Хабы:   Блог компании red_mad_robot , Разработ...   117.94  
1   Хабы:  Блог компании Cloud4Y, Информационная б...    71.07  
2   Хабы:   Блог компании Cloud4Y , Информационная...    71.07  
3   Хабы:   Блог компании Southbridge , Тестирован...   280.79  
4   Хабы:  IT-компании, Управление персоналом, Кар...    145.1  
5   Хабы: Блог компании Альфа-Банк, Искусственный ...   404.32  
6   Хабы:   Блог компании  , Open source , Хранени...   2376.9  
7       Хабы:  Блог компании Хабр, Научно-популярное    353.18  
8   Хабы:  Блог компании , Системное администриров...  2394.92  
9   Хабы:   Мессенджеры , Python , Искусственный и...       14  
10  Хабы:   Блог компании getmatch , Разработка по...   414.35

# Парсинг json файла

In [89]:
all_json = glob.glob(r"Data\*.json")

In [90]:
from types import NoneType
def parse_json(local_data, file_name):
    for i in local_data['refs']:
        all_ref_text.append(i[0])
        all_ref_date.append(f'{i[1]['day']} {i[1]['month']} {i[1]['time']}')
        all_ref_rate.append(i[2]['rate'])
        all_ref_views.append(i[2]['views'])
        result_list['title'].append(file_name)
        result_list['rating'].append(i[2]['rate'])
        result_list['date'].append(f'{i[1]['day']} {i[1]['month']} {i[1]['time']}')
        result_list['description'].append(i[0])
        if type(local_data['info']) is NoneType:
            result_list['tags'].append('Нет тегов')
            all_ref_tags.append('Нет тегов')
        else:
            result_list['tags'].append(local_data['info']['industries'])    
            all_ref_tags.append(local_data['info']['industries'])    

#### Получение информации с файла

In [91]:
data = ['' for i in range(len(all_json))]
all_ref_text = []
all_ref_date = []
all_ref_tags = []
all_ref_rate = []
all_ref_views = []
for i in range(0, len(all_json)-1):
    with open(f'{all_json[i]}', 'r', encoding="utf8") as file:
        data[i] = json.load(file)
for i in range(0, len(data)-1):
    parse_json(data[i], all_json[i])

### Создание датафрейма

In [92]:
df = pd.DataFrame({
    'ref text': all_ref_text,
    'ref day': all_ref_date,
    'ref tags': all_ref_tags,
    'ref rate': all_ref_rate,
    'ref views': all_ref_views
})
df

ref text            ref day  \
0    7 декабря состоялась церемония награждения лау...    8 декабря 09:30   
1    7 декабря состоялась церемония награждения лау...    8 декабря 09:30   
2    Из совместного исследования издателя компьютер...      29 июля 13:50   
3    По статистике The Esports Observer за I полови...       9 июля 09:33   
4    Компании SuperData Research и PayPal провели с...    11 апреля 12:43   
..                                                 ...                ...   
804  С недавних пор на сайте Студии Артемия Лебедев...  13 сентября 13:25   
805  Почти десять лет назад легендарный российский ...   6 сентября 14:46   
806  На сегодняшний день можно разделить рекламные ...   30 августа 00:04   
807  1 сентября 2006 года Студия Артемия Лебедева з...      17 июля 00:02   
808  Павел Гросс, называющий себя известным продавц...      30 июня 03:29   

      ref tags  ref rate  ref views  
0    Нет тегов         6       2300  
1    Нет тегов         6       2300  
2    Нет тегов        12       2800  
3    Нет тегов        18       6200  
4    Нет тегов        11      10000  
..         ...       ...        ...  
804  Нет тегов         0       1200  
805  Нет тегов         0        709  
806  Нет тегов         1        540  
807  Нет тегов         0        696  
808  Нет тегов         0        575  

[809 rows x 5 columns]

### Запись в файл

In [93]:
df.to_csv("json.csv", index=False)
df2 = pd.read_csv("json.csv")
df2.head()

ref text          ref day  \
0  7 декабря состоялась церемония награждения лау...  8 декабря 09:30   
1  7 декабря состоялась церемония награждения лау...  8 декабря 09:30   
2  Из совместного исследования издателя компьютер...    29 июля 13:50   
3  По статистике The Esports Observer за I полови...     9 июля 09:33   
4  Компании SuperData Research и PayPal провели с...  11 апреля 12:43   

    ref tags  ref rate  ref views  
0  Нет тегов         6       2300  
1  Нет тегов         6       2300  
2  Нет тегов        12       2800  
3  Нет тегов        18       6200  
4  Нет тегов        11      10000

In [94]:
file_name = 'GamesHabrJson.csv'
df2 = pd.DataFrame(data=result_list)
df2.to_csv(file_name)